<a href="https://colab.research.google.com/github/mbarragan744/proyecto-IA/blob/main/proyecto.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import kagglehub
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score

dataset_path = kagglehub.dataset_download("syedmtalhahasan/global-urban-air-quality-index-dataset-2015-2025")
print("Path to dataset files:", dataset_path)


df = pd.read_csv(dataset_path + "/global_air_quality_dataset.csv")


df.head()


100%|██████████| 85.1k/85.1k [00:00<00:00, 51.1MB/s]

Extracting files...
Path to dataset files: /root/.cache/kagglehub/datasets/syedmtalhahasan/global-urban-air-quality-index-dataset-2015-2025/versions/1


Date         City Country  AQI  PM2.5 (µg/m³)  PM10 (µg/m³)  \
0  2024-01-01     New York     USA   38          120.0         182.9   
1  2024-01-01  Los Angeles     USA  280           38.4          46.9   
2  2024-01-01       London      UK  117          168.1          34.3   
3  2024-01-01      Beijing   China  197           96.8          35.4   
4  2024-01-01        Delhi   India  187           76.2         226.8   

   NO2 (ppb)  SO2 (ppb)  CO (ppm)  O3 (ppb)  Temperature (°C)  Humidity (%)  \
0       24.3       26.0      9.10     153.3              18.6            40   
1       41.8       34.7      3.78     190.7              -2.2            59   
2       81.5        8.2      3.67     105.4              36.3            62   
3       18.5       39.4      9.51      92.8              29.9            32   
4       46.9       17.2      1.02      68.4               9.9            55   

   Wind Speed (m/s)  
0              13.2  
1               9.5  
2               3.4  
3               1.8  
4               3.3

In [5]:
!pip install -U ydata-profiling

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 400.1/400.1 kB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 22.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 687.8/687.8 kB 26.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 79.3 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=e91ac43abd4ad938243859970470fec25c08468e616a98b0d41b9bb4756e7c94
  Stored in directory: /root/.cache/pip/wheels/8d/55/1a/19cd535375ed1ede0c996405ebffe34b196d78e2d9545723a2
Successfully built htmlmin


In [6]:
import ydata_profiling
from ydata_profiling import ProfileReport

profile = ProfileReport(df, title="Reporte de Pandas Profiling")
profile.to_file("reporte_pandas_profiling.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 13/13 [00:00<00:00, 58.71it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
profile.to_notebook_iframe()

In [ ]:

columns = ['PM10 (µg/m³)', 'NO2 (ppb)', 'SO2 (ppb)', 'CO (ppm)', 'O3 (ppb)', 'Temperature (°C)', 'Humidity (%)', 'Wind Speed (m/s)', 'PM2.5 (µg/m³)']
df = df[columns]


df = df.dropna()

print("Número de filas y columnas después de eliminar valores nulos:", df.shape)


df.head()


Número de filas y columnas después de eliminar valores nulos: (3660, 9)


PM10 (µg/m³)  NO2 (ppb)  SO2 (ppb)  CO (ppm)  O3 (ppb)  Temperature (°C)  \
0         182.9       24.3       26.0      9.10     153.3              18.6   
1          46.9       41.8       34.7      3.78     190.7              -2.2   
2          34.3       81.5        8.2      3.67     105.4              36.3   
3          35.4       18.5       39.4      9.51      92.8              29.9   
4         226.8       46.9       17.2      1.02      68.4               9.9   

   Humidity (%)  Wind Speed (m/s)  PM2.5 (µg/m³)  
0            40              13.2          120.0  
1            59               9.5           38.4  
2            62               3.4          168.1  
3            32               1.8           96.8  
4            55               3.3           76.2

In [ ]:

for col in df.columns:
    lower_limit = df[col].quantile(0.01)
    upper_limit = df[col].quantile(0.99)
    df = df[(df[col] >= lower_limit) & (df[col] <= upper_limit)]

print("Número de filas y columnas después de eliminar valores atípicos:", df.shape)

df.head()


Número de filas y columnas después de eliminar valores atípicos: (3134, 9)


PM10 (µg/m³)  NO2 (ppb)  SO2 (ppb)  CO (ppm)  O3 (ppb)  Temperature (°C)  \
0         182.9       24.3       26.0      9.10     153.3              18.6   
1          46.9       41.8       34.7      3.78     190.7              -2.2   
2          34.3       81.5        8.2      3.67     105.4              36.3   
3          35.4       18.5       39.4      9.51      92.8              29.9   
4         226.8       46.9       17.2      1.02      68.4               9.9   

   Humidity (%)  Wind Speed (m/s)  PM2.5 (µg/m³)  
0            40              13.2          120.0  
1            59               9.5           38.4  
2            62               3.4          168.1  
3            32               1.8           96.8  
4            55               3.3           76.2

In [ ]:

def classify_air_quality(pm25):
    if pm25 <= 12:
        return "Buena"
    elif pm25 <= 35.4:
        return "Moderada"
    elif pm25 <= 55.4:
        return "No saludable para grupos sensibles"
    elif pm25 <= 150.4:
        return "No saludable"
    elif pm25 <= 250.4:
        return "Muy no saludable"
    else:
        return "Peligrosa"


df['Calidad del Aire'] = df['PM2.5 (µg/m³)'].apply(classify_air_quality)

df.drop(columns=['PM2.5 (µg/m³)'], inplace=True)

df.head()


PM10 (µg/m³)  NO2 (ppb)  SO2 (ppb)  CO (ppm)  O3 (ppb)  Temperature (°C)  \
0         182.9       24.3       26.0      9.10     153.3              18.6   
1          46.9       41.8       34.7      3.78     190.7              -2.2   
2          34.3       81.5        8.2      3.67     105.4              36.3   
3          35.4       18.5       39.4      9.51      92.8              29.9   
4         226.8       46.9       17.2      1.02      68.4               9.9   

   Humidity (%)  Wind Speed (m/s)                    Calidad del Aire  
0            40              13.2                        No saludable  
1            59               9.5  No saludable para grupos sensibles  
2            62               3.4                    Muy no saludable  
3            32               1.8                        No saludable  
4            55               3.3                        No saludable

from matplotlib import pyplot as plt
_df_0['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_1['PM10 (µg/m³)'].plot(kind='hist', bins=20, title='PM10 (µg/m³)')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_2['NO2 (ppb)'].plot(kind='hist', bins=20, title='NO2 (ppb)')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_3['SO2 (ppb)'].plot(kind='hist', bins=20, title='SO2 (ppb)')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_18['Calidad del Aire'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_18, x='PM10 (µg/m³)', y='Calidad del Aire', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_19['Calidad del Aire'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_19, x='NO2 (ppb)', y='Calidad del Aire', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_20['Calidad del Aire'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_20, x='SO2 (ppb)', y='Calidad del Aire', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:

X = df[['PM10 (µg/m³)', 'NO2 (ppb)', 'SO2 (ppb)', 'CO (ppm)', 'O3 (ppb)', 'Temperature (°C)', 'Humidity (%)', 'Wind Speed (m/s)']]
y = df['Calidad del Aire']

label_encoder = LabelEncoder()
y = label_encoder.fit_transform(y)

scaler = StandardScaler()
X = scaler.fit_transform(X)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

print("Tamaño del conjunto de entrenamiento:", X_train.shape)
print("Tamaño del conjunto de prueba:", X_test.shape)


Tamaño del conjunto de entrenamiento: (2507, 8)
Tamaño del conjunto de prueba: (627, 8)


In [ ]:
knn = KNeighborsClassifier()
knn.fit(X_train, y_train)

y_pred_knn = knn.predict(X_test)

accuracy_knn = accuracy_score(y_test, y_pred_knn)
print(f'Precisión de K-Nearest Neighbors: {accuracy_knn:.4f}')


Precisión de K-Nearest Neighbors: 0.3860


In [ ]:
nb = GaussianNB()
nb.fit(X_train, y_train)

y_pred_nb = nb.predict(X_test)

accuracy_nb = accuracy_score(y_test, y_pred_nb)
print(f'Precisión de Naive Bayes: {accuracy_nb:.4f}')


Precisión de Naive Bayes: 0.3923


In [ ]:
svm = SVC()
svm.fit(X_train, y_train)


y_pred_svm = svm.predict(X_test)

accuracy_svm = accuracy_score(y_test, y_pred_svm)
print(f'Precisión de Support Vector Machine: {accuracy_svm:.4f}')


Precisión de Support Vector Machine: 0.3796


In [ ]:
dt = DecisionTreeClassifier()
dt.fit(X_train, y_train)

y_pred_dt = dt.predict(X_test)


accuracy_dt = accuracy_score(y_test, y_pred_dt)
print(f'Precisión de Árbol de Decisión: {accuracy_dt:.4f}')


Precisión de Árbol de Decisión: 0.3317


In [ ]:
import joblib

joblib.dump(scaler, 'scaler.bin')
print("Scaler guardado como scaler.bin")


joblib.dump(nb, 'naive_bayes_model.bin')
print("Modelo de Naive Bayes guardado como naive_bayes_model.bin")


Scaler guardado como scaler.bin
Modelo de Naive Bayes guardado como naive_bayes_model.bin
